CTM Training (hyperparameters grid/random search)

Combined TM

In [1]:
import pandas as pd
import numpy as np


from contextualized_topic_models.models.ctm import CombinedTM
from contextualized_topic_models.utils.data_preparation import TopicModelDataPreparation
# from contextualized_topic_models.utils.preprocessing import WhiteSpacePreprocessingStopwords

import nltk
import os

from pathlib import Path
import json
from datetime import datetime

import os
os.environ["TOKENIZERS_PARALLELISM"] = "false"          # disable huggingface warning

/root/.local/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
%load_ext autoreload

In [3]:
import sys

sys.path.append('../')

In [4]:
# load the dataset

%autoreload 2
from dataset_loader import GENRES, load_dataset

genre = GENRES.INDIE
unique_list = ['app_id', 'review_text']

dataset_folder = Path(f'../../dataset/topic_modelling/top_11_genres_unique_[{",".join(unique_list)}]')
dataset, dataset_path = load_dataset(genre, dataset_folder)

dataset.info(verbose=True)

Load dataset from: /root/FYP/NLP/dev-workspace/dataset/topic_modelling/top_11_genres_unique_[app_id,review_text]/01_indie.pkl



<class 'pandas.core.frame.DataFrame'>
Index: 740228 entries, 25636 to 4179608
Data columns (total 8 columns):
 #   Column        Non-Null Count   Dtype 
---  ------        --------------   ----- 
 0   index         740228 non-null  int64 
 1   app_id        740228 non-null  int64 
 2   app_name      740228 non-null  object
 3   review_text   740228 non-null  object
 4   review_score  740228 non-null  int64 
 5   review_votes  740228 non-null  int64 
 6   genre_id      740228 non-null  object
 7   category_id   740228 non-null  object
dtypes: int64(4), object(4)
memory usage: 50.8+ MB


In [5]:
# The path of the dataset to be stored to the config file
str(dataset_path.relative_to(dataset_path.parent.parent.parent.parent))

'dataset/topic_modelling/top_11_genres_unique_[app_id,review_text]/01_indie.pkl'

In [6]:
# data preprocessing

import sys
sys.path.append('../../sa/')

%autoreload 2
import str_cleaning_functions

# copied from lda_demo_gridsearch.ipynb
def cleaning(df, review):
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_links(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_links2(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.clean(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.deEmojify(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_non_letters(x))
    df[review] = df[review].apply(lambda x: x.lower())
    df[review] = df[review].apply(lambda x: str_cleaning_functions.unify_whitespaces(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_stopword(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.unify_whitespaces(x))

# def cleaning_strlist(str_list):
#     str_list = list(map(lambda x: clean(x), str_list))
#     str_list = list(map(lambda x: deEmojify(x), str_list))

#     str_list = list(map(lambda x: x.lower(), str_list))
#     str_list = list(map(lambda x: remove_num(x), str_list))
#     str_list = list(map(lambda x: unify_whitespaces(x), str_list))

#     str_list = list(map(lambda x: _deaccent(x), str_list))
#     str_list = list(map(lambda x: remove_non_alphabets(x), str_list))
#     str_list = list(map(lambda x: remove_stopword(x), str_list))
#     return str_list

# copied from bert_demo_gridsearch.ipynb
def cleaning_little(df, review):
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_links(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_links2(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.clean(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.deEmojify(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.unify_whitespaces(x))


In [7]:
# create a copy of the dataset, as we need both untouched text and cleaned text

dataset_preprocessed = dataset.copy()

In [8]:
cleaning(dataset_preprocessed, 'review_text')
cleaning_little(dataset, 'review_text')

In [9]:
X_preprocessed_temp = dataset_preprocessed['review_text'].values
X_temp = dataset['review_text'].values

In [10]:
assert X_temp.shape == X_preprocessed_temp.shape, "X_temp and X_preprocessed_temp should have the same shape. Found: {} and {}".format(X_temp.shape, X_preprocessed_temp.shape)
assert len(X_temp) == len(X_preprocessed_temp), "X_temp and X_preprocessed_temp should have the same length. Found: {} and {}".format(len(X_temp), len(X_preprocessed_temp))

In [11]:
# remove docs with 0 len

X, X_preprocessed = [], []

for i, (doc, doc_preprocessed) in enumerate(zip(list(X_temp), list(X_preprocessed_temp))):
    if len(doc) == 0 or len(doc_preprocessed) == 0:
        continue

    X.append(doc)
    X_preprocessed.append(doc_preprocessed)

In [12]:
assert len(X) == len(X_preprocessed), "X and X_preprocessed should have the same length. Found: {} and {}".format(len(X), len(X_preprocessed))

Apply lemmatizing to the preprocessed dataset as well (for BoW)

The function is identical in LDA

In [13]:
# do lemmatization, but not stemming (as part of speech is important in topic modelling)
# use nltk wordnet for lemmatization

from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet

lemma = WordNetLemmatizer()

# from https://stackoverflow.com/questions/25534214/nltk-wordnet-lemmatizer-shouldnt-it-lemmatize-all-inflections-of-a-word

# from: https://www.cnblogs.com/jclian91/p/9898511.html
def get_wordnet_pos(tag):
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return None     # if none -> created as noun by wordnet
    
def lemmatization(text):
   # use nltk to get PoS tag
    tagged = nltk.pos_tag(nltk.word_tokenize(text))

    # then we only need adj, adv, verb, noun
    # convert from nltk Penn Treebank tag to wordnet tag
    wn_tagged = list(map(lambda x: (x[0], get_wordnet_pos(x[1])), tagged))

    # lemmatize by the PoS
    lemmatized = list(map(lambda x: lemma.lemmatize(x[0], pos=x[1] if x[1] else wordnet.NOUN), wn_tagged))
    # lemma.lemmatize(wn_tagged[0], pos=wordnet.NOUN)

    return lemmatized

In [14]:
X_preprocessed = list(map(lambda x: lemmatization(x), X_preprocessed))
X_preprocessed = list(map(lambda x: ' '.join(x), X_preprocessed))

Training

In [15]:
# copy from: https://github.com/MilaNLProc/contextualized-topic-models/blob/master/contextualized_topic_models/utils/data_preparation.py#L44
# call bert_embeddings_from_list() to produce embeddings by ourself

import warnings
from sentence_transformers import SentenceTransformer
import torch
import platform


if platform.system() == 'Linux' or platform.system() == 'Windows':
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
else:
    device = torch.device('mps')        # m-series mac machine

print(device)


# moved the functions ctm_dataset_creation.py
from ctm_dataset_creation import bert_embeddings_from_list

cuda


In [16]:
from gensim.models import CoherenceModel
from copy import deepcopy

from sklearn.model_selection import ParameterGrid, ParameterSampler

sys.path.append('../')

from eval_metrics import compute_inverted_rbo, compute_topic_diversity, compute_pairwise_jaccard_similarity, \
                        METRICS, SEARCH_BEHAVIOUR, COHERENCE_MODEL_METRICS

In [17]:
def _print_message(message):
    '''Print message with a timestamp in front of it

    Timestamp format: YYYY-MM-DD HH:MM:SS,mmm
    '''
    print(f'{datetime.now().strftime("%Y-%m-%d %H:%M:%S,%f")[:-3]} - {message}')

In [18]:
# init params

def _init_count_vectorizer_params(
        max_features=2000,
        ngram_range=(1,1)
):
    params_dict = {}
    params_dict['max_features'] = max_features
    params_dict['ngram_range'] = ngram_range

    return params_dict

def _init_sbert_params(
    model_name_or_path='all-mpnet-base-v2'
):
    params_dict = {}
    params_dict['model_name_or_path'] = model_name_or_path

    return params_dict

# params are copied from source code of CTM: https://github.com/MilaNLProc/contextualized-topic-models/blob/master/contextualized_topic_models/models/ctm.py#L131
# commented params are params that has no plan on fine-tuning them (not significant to our project)
def _init_ctm_params(
        # bow_size,
        # contextual_size,
        # inference_type="combined",
        n_components=10,
        # model_type="prodLDA",
        hidden_sizes=[100, 100],        # pass as list as json does not support tuple
        # activation="softplus",
        dropout=0.2,
        # learn_priors=True,
        # batch_size=64,
        lr=2e-3,
        momentum=0.99,
        solver="adam",
        num_epochs=100,
        # reduce_on_plateau=False,      # only valid if there's a testing data (seems no need to havbe label, just partition a testing dataset with train_test_split()))
        # num_data_loader_workers=mp.cpu_count(),
        # label_size=0,
        # loss_weights=None
):
    params_dict = {}
    # params_dict['bow_size'] = bow_size                        # decided by the count vectorizer params (max_features)
    # params_dict['contextual_size'] = contextual_size          # decided by the sbert model
    # params_dict['inference_type'] = inference_type
    params_dict['n_components'] = n_components
    # params_dict['model_type'] = model_type
    params_dict['hidden_sizes'] = hidden_sizes
    # params_dict['activation'] = activation
    params_dict['dropout'] = dropout
    # params_dict['learn_priors'] = learn_priors
    # params_dict['batch_size'] = batch_size
    params_dict['lr'] = lr
    params_dict['momentum'] = momentum
    params_dict['solver'] = solver
    params_dict['num_epochs'] = num_epochs

    return params_dict

In [19]:
def _init_config_dict(config_path:Path, model_name:str, dataset_path:Path, hyperparameters:dict, search_space_dict:dict, 
                      metrics:list[METRICS], monitor:METRICS,
                      search_behaviour:SEARCH_BEHAVIOUR, search_rs:int, search_n_iter:int):
    
    if not config_path.exists():
        config = {}

        sbert_params = _init_sbert_params(**hyperparameters['sbert_params'])
        countvect_params = _init_count_vectorizer_params(**hyperparameters['countvect_params'])
        ctm_params = _init_ctm_params(**hyperparameters['ctm_params'])

        config['model'] = model_name
        config['dataset_path'] = str(dataset_path)
        config['sbert_params'] = sbert_params
        config['countvect_params'] = countvect_params
        config['ctm_params'] = ctm_params

        if 'sbert_params' in search_space_dict:
            for k in search_space_dict['sbert_params'].keys():
                sbert_params.pop(k, '')     # add a default value to avoid key error
        if 'countvect_params' in search_space_dict:
            for k in search_space_dict['countvect_params'].keys():
                countvect_params.pop(k, '')
        if 'ctm_params' in search_space_dict:
            for k in search_space_dict['ctm_params'].keys():
                ctm_params.pop(k, '')

        config['search_space'] = search_space_dict
        config['metrics'] = list(map(lambda x: x.value, metrics))
        config['monitor'] = monitor.value

        config['search_behaviour'] = search_behaviour.value
        if search_behaviour == SEARCH_BEHAVIOUR.RANDOM_SEARCH:
            config['search_rs'] = search_rs
            config['search_n_iter'] = search_n_iter

        with open(config_path, 'w') as f:
            json.dump(config, f, indent=2)

        _print_message('Created config file at {}'.format(config_path))
        # print('Created config file at {}'.format(config_path))
    else:
        with open(config_path, 'r') as f:
            config = json.load(f)

        # check whether the input params are consistent with the config file
        assert config['model'] == model_name, 'input model_name is not consistent with the config["model"]'
        assert config['dataset_path'] == str(dataset_path), 'input dataset_path is not consistent with the config["dataset_path"]'
        assert config['metrics'] == list(map(lambda x: x.value, metrics)), 'input metrics is not consistent with config["metrics"]'
        assert config['monitor'] == monitor.value, 'input monitor is not consistent with config["monitor"]'
        assert config['search_behaviour'] == search_behaviour.value, 'input search_behaviour is not consistent with config["search_behaviour"]'
        if search_behaviour == SEARCH_BEHAVIOUR.RANDOM_SEARCH:
            assert config['search_rs'] == search_rs, 'input search_rs is not consistent with config["search_rs"]'
            assert config['search_n_iter'] == search_n_iter, 'input search_n_iter is not consistent with config["search_n_iter"]'

        # check whether the hyperparameters are consistent with the config file
        sbert_params = _init_sbert_params(**hyperparameters['sbert_params'])
        countvect_params = _init_count_vectorizer_params(**hyperparameters['countvect_params'])
        ctm_params = _init_ctm_params(**hyperparameters['ctm_params'])

        assert config['sbert_params'].keys() <= sbert_params.keys(), 'existing config["sbert_params"] contains additional hyperparameters'
        assert config['countvect_params'].keys() <= countvect_params.keys(), 'existing config["countvect_params"] contains additional hyperparameters'
        assert config['ctm_params'].keys() <= ctm_params.keys(), 'existing config["ctm_params"] contains additional hyperparameters'

        for key in sbert_params.keys() & config['sbert_params'].keys():
            assert sbert_params[key] == config['sbert_params'][key], 'existing config["sbert_params"] contains different hyperparameters'
        for key in countvect_params.keys() & config['countvect_params'].keys():
            assert countvect_params[key] == config['countvect_params'][key], 'existing config["countvect_params"] contains different hyperparameters'
        for key in ctm_params.keys() & config['ctm_params'].keys():
            assert ctm_params[key] == config['ctm_params'][key], 'existing config["ctm_params"] contains different hyperparameters'

        # check whether the search_space is consistent with the config file
        if 'sbert_params' in config['search_space']:
            assert config['search_space']['sbert_params'].keys() == search_space_dict['sbert_params'].keys(), 'input search_space_dict["sbert_params"] contains different hyperparameter keys than existing config["search_space"]["sbert_params"]'
            for k in search_space_dict['sbert_params'].keys():
                assert k in config['search_space']['sbert_params'], f'input search_space_dict["sbert_params"]["{key}"] contains value than existing config["search_space"]["sbert_params"]["{key}"]'
        if 'countvect_params' in config['search_space']:
            assert config['search_space']['countvect_params'].keys() == search_space_dict['countvect_params'].keys(), 'input search_space_dict["countvect_params"] contains different hyperparameter keys than existing config["search_space"]["countvect_params"]'
            for k in search_space_dict['countvect_params'].keys():
                assert k in config['search_space']['countvect_params'], f'input search_space_dict["countvect_params"]["{key}"] contains value than existing config["search_space"]["countvect_params"]["{key}"]'
        if 'ctm_params' in config['search_space']:
            assert config['search_space']['ctm_params'].keys() == search_space_dict['ctm_params'].keys(), 'input search_space_dict["ctm_params"] contains different hyperparameter keys than existing config["search_space"]["ctm_params"]'
            for k in search_space_dict['ctm_params'].keys():
                assert k in config['search_space']['ctm_params'], f'input search_space_dict["ctm_params"]["{key}"] contains value than existing config["search_space"]["ctm_params"]["{key}"]'
        
        _print_message('Loaded existing config file from {}'.format(config_path))
        _print_message('Hyperparameters and search space are consistent with the input parameters')
        # print('Loaded existing config file from {}'.format(config_path))
        # print('Hyperparameters and search space are consistent with the input parameters')

    return config


In [20]:
def _init_result_dict(result_path:Path, monitor_type:str):
    if not result_path.exists():
        result = {}

        result['best_metric'] = -float('inf')
        result['best_model_checkpoint'] = ""
        result['best_hyperparameters'] = dict()
        result["monitor_type"] = monitor_type
        result["log_history"] = list()

    else:
        with open(result_path, 'r') as f:
            result = json.load(f)

        assert result['monitor_type'] == monitor_type

        _print_message('Loaded existing result file from {}'.format(result_path))
        # print('Loaded existing result file from {}'.format(result_path))
    
    return result

In [21]:
from ctm_utils import _load_ctm_model

# their implementation is moved to utils script as it is also used in eval script.

In [22]:
from ctm_utils import _get_topics, _get_topic_word_metrix, _get_topic_document_metrix

# their implementation is moved to utils script as it may be used in eval script.

In [23]:
import pickle
from gensim import corpora
# from sklearn.feature_extraction.text import CountVectorizer, ENGLISH_STOP_WORDS
# from contextualized_topic_models.datasets.dataset import CTMDataset

%autoreload 2
from ctm_dataset_creation import create_ctm_dataset

def model_search(X_contextual, X_bow, hyperparameters:dict, search_space:dict, save_folder:Path, dataset_path:Path,
                 additional_stopwords:list[str]=None,
                 metrics:list[METRICS]=[METRICS.C_NPMI], monitor:METRICS=METRICS.C_NPMI, 
                 save_each_models=True, run_from_checkpoints=False,
                 search_behaviour=SEARCH_BEHAVIOUR.GRID_SEARCH, search_rs=42, search_n_iter=10):
    
    config_json_path = save_folder.joinpath('config.json')
    result_json_path = save_folder.joinpath('result.json')

    if monitor not in metrics:
        raise Exception('monitor is not in metrics. Please modify the metrics passed in.')

    if run_from_checkpoints:
        if not save_folder.exists():
            _print_message('Save folder:' + str(save_folder.resolve()) + ' does not exist. Function terminates.')
            # print('Save folder:' + str(save_folder.resolve()) + ' does not exist. Function terminates.')
            raise Exception('No checkpoints found. Function terminates.')
        
        # check for existing configs
        if not config_json_path.exists():
            raise Exception('No config.json found. Function terminates.')
        
        # check for existing results
        if not result_json_path.exists():
            _print_message('No result.json is found. Assuming no existing checkpoints.')
            # print('No result.json is found. Assuming no existing checkpoints.')
    else:
        if save_folder.exists():
            raise Exception('Checkpoints found. Please delete the checkpoints or set run_from_checkpoints=True. Function terminates.')

    if not save_folder.exists():
        save_folder.mkdir()

    config = _init_config_dict(config_json_path, 'ctm', dataset_path, hyperparameters, search_space,
                               metrics, monitor, search_behaviour, search_rs, search_n_iter)
    result = _init_result_dict(result_json_path, monitor.value)

    _print_message('Search folder: {}'.format(save_folder))
    # print('Search folder: {}'.format(save_folder))

    # init
    best_model_path = result['best_model_checkpoint']
    best_metric_score = result['best_metric']
    best_model = _load_ctm_model(Path(best_model_path),
                                 result['best_hyperparameters']['ctm_params']) if best_model_path != "" else None
    best_hyperparameters = result['best_hyperparameters']


    _print_message('Best model checkpoint: {}'.format(best_model_path))
    _print_message('Best metric score: {}'.format(best_metric_score))
    _print_message('Best model: {}'.format(best_model))
    # print(f'Best model checkpoint: {best_model_path}')
    # print(f'Best metric score: {best_metric_score}')
    # print(f'Best model: {best_model}')

    # search
    # like bertopic, we create a temp dict for initiating the search space
    # then we apply sklearn parameter sampler / parameter grid to get the search space
    temp_search_space = {}
    for k, v in search_space.items():
        for kk, vv in v.items():
            temp_search_space[k + '__' + kk] = vv

    if search_behaviour == SEARCH_BEHAVIOUR.RANDOM_SEARCH:
        search_iterator = ParameterSampler(temp_search_space, search_n_iter, random_state=search_rs)
    elif search_behaviour == SEARCH_BEHAVIOUR.GRID_SEARCH:
        search_iterator = ParameterGrid(temp_search_space)

    print('\n')

    for search_space_dict in search_iterator:

        # unwrap the search space dict

        model_name = ''

        _sbert_params = {}
        _countvect_params = {}
        _ctm_params = {}

        for k, v in search_space_dict.items():
            if k.startswith('sbert_params'):
                _sbert_params[k.split('__')[1]] = v
                model_name += 'sb_' + k.split('__')[1] + '_' + str(v) + '_'
            elif k.startswith('countvect_params'):
                _countvect_params[k.split('__')[1]] = v
                model_name += 'cvect_' + k.split('__')[1] + '_' + str(v) + '_'
            elif k.startswith('ctm_params'):
                _ctm_params[k.split('__')[1]] = v
                model_name += 'ctm_' + k.split('__')[1] + '_' + str(v) + '_'

        model_name = model_name[:-1]     # remove the last '_'

        model_path = save_folder.joinpath(config['model'] + '_' + model_name)

        # check whether the model exists
        if model_path.exists():
            _print_message('Skipping current search space: {}'.format(search_space_dict))
            # print('Skipping current search space: {}'.format(search_space_dict))
            continue

    
        ##########
        # Training starts
        ##########

        _print_message('Current search space: {}'.format(search_space_dict))
        # print('Current search space: {}'.format(search_space_dict))

        sbert_params = deepcopy(config['sbert_params'])     # deepcopy just for safety (not messing up with the original config)
        countvect_params = deepcopy(config['countvect_params'])
        ctm_params = deepcopy(config['ctm_params'])

        sbert_params.update(_sbert_params)
        countvect_params.update(_countvect_params)
        ctm_params.update(_ctm_params)

        countvect_params['ngram_range'] = tuple(countvect_params['ngram_range'])     # convert list to tuple

        ##########
        # Preprocessing
        ##########

        # for re-producting the result (and inferencing)
        # we need to load the vectorizer, do the exact steps in preprocessing for creating bow
        # then create a CTMDataset for inferencing

        # create bow
        # vectorizer = CountVectorizer(
        #     stop_words="english" if additional_stopwords is None else list(ENGLISH_STOP_WORDS.union(additional_stopwords)),
        #     analyzer='word',
        #     **countvect_params)
        
        # vectorizer = vectorizer.fit(X_bow)
        # vocab = vectorizer.get_feature_names_out()
        # vocab_set = set(vocab)

        # preprocessed_docs_tmp = [' '.join([w for w in doc.split() if w in vocab_set])
        #                     for doc in X_bow]
        
        # text_for_contextual, text_for_bow = [], []
        # X_tmp = []

        
        # assert len(X_contextual) == len(preprocessed_docs_tmp), f'len(text_for_contextual): {len(X_contextual)}, len(preprocessed_docs_tmp): {len(preprocessed_docs_tmp)}'
        # assert len(X) == len(X_contextual), f'len(X): {len(X)}, len(text_for_contextual): {len(X_contextual)}'
        
        # # remove empty docs
        # for i, (tfc, tfb) in enumerate(zip(X_contextual, preprocessed_docs_tmp)):
        #     if len(tfb) == 0 or len(tfc) == 0:
        #         continue
                
        #     text_for_contextual.append(tfc)
        #     text_for_bow.append(tfb)
        #     X_tmp.append(X[i])

        # assert len(text_for_contextual) == len(text_for_bow), f'len(text_for_contextual_tmp): {len(text_for_contextual)}, len(text_for_bow_tmp): {len(text_for_bow)}'
        # assert len(X_tmp) == len(text_for_contextual), f'len(X_tmp): {len(X_tmp)}, len(text_for_contextual_tmp): {len(text_for_contextual)}'


        # train_bow_embeddings = vectorizer.transform(text_for_bow)

        
        # # isntead of using default TopicModelDataPreparation(), build the dataset by referencing the source code of it
        # # source code: https://github.com/MilaNLProc/contextualized-topic-models/blob/master/contextualized_topic_models/utils/data_preparation.py
        # # according to the source code, we only need to create the idx2token, then use the countvectorizer above to build the dataset
        # idx2token = {k: v for k, v in zip(range(0, len(vocab)), vocab)}

        
        # # create sbert embeddings
        # if platform.system() == 'Linux' or platform.system() == 'Windows':
        #     device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        # else:
        #     device = torch.device('mps')        # m-series machine
        

        # # check existing embeddings
        # # reuse them if found
        # embeddings_path = save_folder.joinpath(f'embeddings_{sbert_params["model_name_or_path"]}.pkl')
        # if embeddings_path.exists():
        #     with open(embeddings_path, 'rb') as f:
        #         embeddings = np.load(f)

        #     assert embeddings.shape[0] == len(text_for_contextual), f'embeddings.shape[0]: {embeddings.shape[0]}, len(text_for_contextual): {len(text_for_contextual)}'

        #     _print_message(f'Found existing sbert embeddings at {embeddings_path}. Reusing them.')
        #     # print(f'Found existing sbert embeddings at {embeddings_path}. Reusing them.')
        # else:
        #     embeddings = bert_embeddings_from_list(text_for_contextual, **sbert_params, device=device)

        #     with open(embeddings_path, 'wb') as f:
        #         np.save(f, embeddings)
         


        # # tp = TopicModelDataPreparation()
        # # training_dataset = tp.fit(text_for_contextual=text_for_contextual, text_for_bow=text_for_bow, custom_embeddings=embeddings)
        # training_dataset = CTMDataset(
        #     X_contextual=embeddings,
        #     X_bow=train_bow_embeddings,
        #     idx2token=idx2token,
        #     labels=None
        # )

        training_dataset, vectorizer, embeddings, X_tmp = create_ctm_dataset(
            X_contextual, X_bow, X,
            sbert_params, save_folder,
            vectorizer=None,            # pass None to ask the function to create a new sklearn CountVectorizer
            countvect_params=countvect_params,
            additional_stopwords=additional_stopwords)

        vocab = vectorizer.get_feature_names_out()
        
        # ctm

        ctm_params['bow_size'] = len(vocab)
        ctm_params['contextual_size'] = embeddings.shape[1]
        ctm_params['hidden_sizes'] = tuple(ctm_params['hidden_sizes'])     # convert list to tuple

        ctm = CombinedTM(**ctm_params)
        ctm.device = device
        ctm.fit(training_dataset, verbose=True)

        ##########
        # Training ends
        ##########

        ##########
        # Evaluation starts
        ##########

        # init data for gensim coherence model
        topic_words = _get_topics(ctm, k=10)
        topics = ctm.get_predicted_topics(training_dataset, n_samples=20)

        documents = pd.DataFrame({"Document": X_tmp,
                                "ID": range(len(X_tmp)),
                                "Topic": topics})
        
        docs_per_topic = documents.groupby(['Topic'], as_index=False).agg({'Document': ' '.join})
        texts = [doc.split() for doc in docs_per_topic.Document.values]
        
        dictionary = corpora.Dictionary(texts)
        corpus = [dictionary.doc2bow(text) for text in texts]

        # init octis format result for convenience
        result_octis = {}
        result_octis['topics'] = topic_words
        result_octis['topic-word-matrix'] = _get_topic_word_metrix(ctm)
        result_octis['topic-document-matrix'] = _get_topic_document_metrix(ctm, training_dataset, n_samples=20)

        _print_message('Compute evaluation metrics')
        # print('Compute evaluation metrics')

        metrics_score = dict()

        for metric in metrics:
            if metric in COHERENCE_MODEL_METRICS:
                coherencemodel = CoherenceModel(
                    topics=topic_words, 
                    texts=texts, 
                    corpus=corpus, 
                    dictionary=dictionary, 
                    coherence=metric.value, 
                    topn=10,
                    processes=3
                )
                score = coherencemodel.get_coherence()
            elif metric == METRICS.TOPIC_DIVERSITY:
                score = compute_topic_diversity(result_octis, topk=10)
            elif metric == METRICS.INVERTED_RBO:
                score = compute_inverted_rbo(result_octis, topk=10)
            elif metric == METRICS.PAIRWISE_JACCARD_SIMILARITY:
                score = compute_pairwise_jaccard_similarity(result_octis, topk=10)
            else:
                raise Exception('Unknown metric: {}'.format(metric.value))

            metrics_score[metric.value] = score

            _print_message('Evaluation metric ({}): {}'.format(metric.value, score))
            # print(f'Evaluation metric ({metric.value}): {score}')

        monitor_score = metrics_score[monitor.value]

        ##########
        # Evaluation ends
        ##########

        ##########
        # Save models
        ##########

        if not model_path.exists():
            model_path.mkdir()
        
        if save_each_models:
            ctm.save(models_dir=model_path)

        # save the vectorizer
        # then we can reproduce the result better
        vectorizer_path = model_path.joinpath('count_vectorizer.pkl')
        with open(vectorizer_path, 'wb') as f:
            pickle.dump(vectorizer, f)
        

        ##########
        # Save models ends
        ##########

        ###########
        # Update result dict and json file
        ###########
            
        model_hyperparameters = {
            'sbert_params': sbert_params,
            'countvect_params': countvect_params,
            'ctm_params': ctm_params
        }

        if monitor_score > best_metric_score:
            best_metric_score = monitor_score
            best_model_path = model_path
            best_model = ctm
            best_hyperparameters = model_hyperparameters

        model_log_history = dict()
        model_log_history.update(metrics_score)
        model_log_history['model_name'] = model_name
        model_log_history['hyperparameters']  = model_hyperparameters

        result['best_metric'] = best_metric_score
        result['best_model_checkpoint'] = str(best_model_path)
        result['best_hyperparameters'] = best_hyperparameters
        result['log_history'].append(model_log_history)

        # save result
        with open(result_json_path, 'w') as f:
            json.dump(result, f, indent=2)

        _print_message('Saved result.json at: {}'.format(result_json_path))        
        # print('Saved result.json at:', result_json_path)
        print('\n\n')
    
    _print_message('Search ends')
    # print('Search ends')
    return best_model, best_model_path, best_hyperparameters


In [24]:
# load/create custom stopwords stored in a txt from dataset folder
from pathlib import Path

custom_stopwords_path = Path('../../dataset/topic_modelling/stopwords.txt')
custom_stowords_games_path = Path('../../dataset/topic_modelling/stopwords_games.txt')
game_name_list_path = Path('../../dataset/topic_modelling/game_name_list.txt')

with open(custom_stopwords_path, 'r') as f:
    custom_stopwords = f.read().splitlines()

with open(custom_stowords_games_path, 'r') as f:
    custom_stowords_games = f.read().splitlines()

with open(game_name_list_path, 'r') as f:
    game_name_list = f.read().splitlines()

# also include the stopword list from nltk
from nltk.corpus import stopwords
nltk_stopwords = stopwords.words('english')

custom_stopwords = custom_stopwords + custom_stowords_games + game_name_list + nltk_stopwords
custom_stopwords = list(filter(lambda x: len(x) > 0, custom_stopwords))     # remove empty string
custom_stopwords = set(custom_stopwords)

print(custom_stopwords)
print(len(custom_stopwords))


{'mixed estate', 'pikuniku', 'new terra®', 'variety costume set', 'pass the light', 'amnesia fortnight: af 2017 - day 0', 'seen', 'sea birds: end of an age', 'spiky situation playtest', 'mobmania', 'crawlyard', 'battlestar galactica deadlock: reinforcement pack', 'grot slasher', 'trophy knight', 'planet guardian vr', 'my summer car', '飄流幻境', 'warfield - multiplayer', 'the book of aaru', 'lucky player', 'boxit levelpack #2', 'the ghost and the golem', 'indie pogo: money-themed emblems', 'pseudoregalia', 'การิน ปริศนาคดีอาถรรพ์ the game : ตอนพิธีเปลี่ยนชีพ', 'cat city', 'strange brigade - the thrice damned 3: great pyramid of bes', 'survivors of the dawn demo', 'raindrops', 'android john 2.1 demo', 'fishing planet: holiday pack', 'goliath: playing with reality', 'pincol', 'zombie army 4: mission 9 - return to hell', 'stray blade', 'heist', 'the outbreak guardian', '2k11', 'world of borecraft', 'fsx steam edition: cessna® c188 agtruck add-on', 'warp lab', 'samurai of hyuga book 4 - side s

In [26]:
# grid search / random search

# hyperparameters
sbert_params = _init_sbert_params(model_name_or_path='all-mpnet-base-v2')
countvect_params = _init_count_vectorizer_params(max_features=2000, ngram_range=[1,1])
ctm_params = _init_ctm_params(
    n_components=10, 
    hidden_sizes=[100, 100], 
    dropout=0.2, lr=2e-3, momentum=0.99, solver="adam", 
    num_epochs=25       # original default value is 100 (in LDAProd), some tested with 50
)

search_space_dict = {
    'sbert_params': {
        'model_name_or_path': ['all-MiniLM-L6-v2']
    },
    # 'countvect_params': {
    #     'max_features' : [1500, 2000, 2500],
    #     'ngram_range': [[1, 1], [1, 2]]     # datatype is list as json does not support tuple
    # },
    'ctm_params':{
        'n_components': [10, 20, 30, 40, 50, 60, 70, 80, 90, 100],
        # 'hidden_sizes': [(100, 100), (200, 200), (100, 100, 100), (200, 200, 200)],
        # 'num_epochs':[50]
    }
}

dataset_path_config = dataset_path.relative_to(dataset_path.parent.parent.parent.parent)

search_behaviour = SEARCH_BEHAVIOUR.GRID_SEARCH
# search_behaviour = SEARCH_BEHAVIOUR.RANDOM_SEARCH

# training_datetime = datetime.now()
training_datetime = datetime(2024, 2, 4, 8, 7, 27)
training_folder = Path(f'ctm_genre_{str(genre)}_{search_behaviour.value}_{training_datetime.strftime("%Y%m%d_%H%M%S")}')

best_model, best_model_path, best_hyperparameters = model_search(
    X,
    X_preprocessed,
    hyperparameters={
        'sbert_params': sbert_params,
        'countvect_params': countvect_params,
        'ctm_params': ctm_params
    },
    search_space=search_space_dict,
    save_folder=training_folder,
    dataset_path=dataset_path_config,
    metrics=[METRICS.C_NPMI, METRICS.C_V, METRICS.UMASS, METRICS.C_UCI, METRICS.TOPIC_DIVERSITY, METRICS.INVERTED_RBO, METRICS.PAIRWISE_JACCARD_SIMILARITY],
    monitor=METRICS.C_NPMI,
    save_each_models=True,
    run_from_checkpoints=True,
    search_behaviour=search_behaviour,
    # search_rs=42,
    # search_n_iter=50
)

2024-02-04 12:12:54,753 - Loaded existing config file from ctm_genre_indie_grid_search_20240204_080727/config.json
2024-02-04 12:12:54,753 - Hyperparameters and search space are consistent with the input parameters
2024-02-04 12:12:54,754 - Loaded existing result file from ctm_genre_indie_grid_search_20240204_080727/result.json
2024-02-04 12:12:54,754 - Search folder: ctm_genre_indie_grid_search_20240204_080727


/root/miniforge3/envs/fyp-test-wsl-tm/lib/python3.9/site-packages/contextualized_topic_models/models/ctm.py:669: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  warnings.warn(


2024-02-04 12:12:55,310 - Best model checkpoint: ctm_genre_indie_grid_search_20240204_080727/ctm_ctm_n_components_40_sb_model_name_or_path_all-MiniLM-L6-v2
2024-02-04 12:12:55,310 - Best metric score: 0.01933024454191077
2024-02-04 12:12:55,310 - Best model: <contextualized_topic_models.models.ctm.CombinedTM object at 0x7f6190ac9e80>


2024-02-04 12:12:55,311 - Skipping current search space: {'ctm_params__n_components': 10, 'sbert_params__model_name_or_path': 'all-MiniLM-L6-v2'}
2024-02-04 12:12:55,311 - Skipping current search space: {'ctm_params__n_components': 20, 'sbert_params__model_name_or_path': 'all-MiniLM-L6-v2'}
2024-02-04 12:12:55,311 - Skipping current search space: {'ctm_params__n_components': 30, 'sbert_params__model_name_or_path': 'all-MiniLM-L6-v2'}
2024-02-04 12:12:55,311 - Skipping current search space: {'ctm_params__n_components': 40, 'sbert_params__model_name_or_path': 'all-MiniLM-L6-v2'}
2024-02-04 12:12:55,311 - Current search space: {'ctm_params__n_components': 5

Epoch: [25/25]	 Seen Samples: [18222400/18223400]	Train Loss: 168.42902921836907	Time: 0:00:39.490632: : 25it [16:36, 39.85s/it]
100%|██████████| 11390/11390 [00:21<00:00, 520.02it/s]


2024-02-04 12:31:13,094 - Compute evaluation metrics
2024-02-04 12:33:27,209 - Evaluation metric (c_npmi): 0.011329266331606882
2024-02-04 12:38:07,471 - Evaluation metric (c_v): 0.47283345141025485
2024-02-04 12:38:07,775 - Evaluation metric (u_mass): -0.060415580848927466
2024-02-04 12:40:21,785 - Evaluation metric (c_uci): -0.5051054979166154
2024-02-04 12:40:21,785 - Evaluation metric (topic_diversity): 0.622
2024-02-04 12:40:21,824 - Evaluation metric (inverted_rbo): 0.9711130320476151
2024-02-04 12:40:21,825 - Evaluation metric (pairwise_jaccard_similarity): 0.020500362859622378


...

2024-02-04 14:27:26,412 - Saved result.json at: ctm_genre_indie_grid_search_20240204_080727/result.json



2024-02-04 14:27:26,412 - Current search space: {'ctm_params__n_components': 100, 'sbert_params__model_name_or_path': 'all-MiniLM-L6-v2'}
Settings: 
                   N Components: 100
                   Topic Prior Mean: 0.0
                   Topic Prior Variance: 0.99
                   Model Type: prodLDA
                   Hidden Sizes: (100, 100)
                   Activation: softplus
                   Dropout: 0.2
                   Learn Priors: True
                   Learning Rate: 0.002
                   Momentum: 0.99
                   Reduce On Plateau: False
                   Save Dir: None


Epoch: [25/25]	 Seen Samples: [18222400/18223400]	Train Loss: 186.17639464621945	Time: 0:00:42.451558: : 25it [18:10, 43.62s/it]
100%|██████████| 11390/11390 [00:24<00:00, 466.87it/s]


2024-02-04 14:47:25,456 - Compute evaluation metrics
2024-02-04 14:48:54,524 - Evaluation metric (c_npmi): 0.012973577720398194
2024-02-04 14:52:13,872 - Evaluation metric (c_v): 0.46226113497706073
2024-02-04 14:52:14,229 - Evaluation metric (u_mass): -0.07524340283377164
2024-02-04 14:53:41,711 - Evaluation metric (c_uci): -0.39351829311707787
2024-02-04 14:53:41,711 - Evaluation metric (topic_diversity): 0.391
2024-02-04 14:53:41,867 - Evaluation metric (inverted_rbo): 0.941424369375951
2024-02-04 14:53:41,870 - Evaluation metric (pairwise_jaccard_similarity): 0.03870821358437506


/root/miniforge3/envs/fyp-test-wsl-tm/lib/python3.9/site-packages/contextualized_topic_models/models/ctm.py:640: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  warnings.warn(


2024-02-04 14:53:43,306 - Saved result.json at: ctm_genre_indie_grid_search_20240204_080727/result.json



2024-02-04 14:53:43,306 - Search ends


In [33]:
# load the model from disk to compare the results

search_behaviour = SEARCH_BEHAVIOUR.GRID_SEARCH
training_datetime = datetime(2024, 1, 29, 21, 29, 10)
training_folder = Path(f'ctm_{search_behaviour.value}_{training_datetime.strftime("%Y%m%d_%H%M%S")}')

training_result_json_path = training_folder.joinpath('result.json')
with open(training_result_json_path, 'r') as f:
    training_result = json.load(f)


# load the embeddings
model_name_or_path = training_result['best_hyperparameters']['sbert_params']['model_name_or_path']
embeddings_path = training_folder.joinpath(f'embeddings_{model_name_or_path}.pkl')
with open(embeddings_path, 'rb') as f:
    embeddings = np.load(f)

best_model_path = training_result['best_model_checkpoint']
ctm_hyperparameters = training_result['best_hyperparameters']['ctm_params']
sbert_params = training_result['best_hyperparameters']['sbert_params']

# ctm_hyperparameters['bow_size'] = 2000
# ctm_hyperparameters['contextual_size'] = 768

best_model_loaded = _load_ctm_model(Path(best_model_path), ctm_hyperparameters)

# create the dataset on the fly
vectorizer = pickle.load(open(Path(best_model_path).joinpath('count_vectorizer.pkl'), 'rb'))

training_dataset, _, _, _ = create_ctm_dataset(
    X, X_preprocessed, 
    sbert_params, training_folder,
    vectorizer=vectorizer)


doc_topic_dist_1 = best_model.get_doc_topic_distribution(training_dataset, n_samples=20)
doc_topic_dist_2 = best_model_loaded.get_doc_topic_distribution(training_dataset, n_samples=20)

/root/miniforge3/envs/fyp-test-wsl-tm/lib/python3.9/site-packages/contextualized_topic_models/models/ctm.py:669: Warning: This is an experimental feature that we has not been fully tested. Refer to the following issue:https://github.com/MilaNLProc/contextualized-topic-models/issues/38
  warnings.warn(
/tmp/ipykernel_121544/4160714911.py:28: ResourceWarning: unclosed file <_io.BufferedReader name='ctm_grid_search_20240129_212910/ctm_ctm_n_components_50_sb_model_name_or_path_all-MiniLM-L6-v2/count_vectorizer.pkl'>
  vectorizer = pickle.load(open(Path(best_model_path).joinpath('count_vectorizer.pkl'), 'rb'))


2024-01-30 00:31:25,572 - Found existing sbert embeddings at ctm_grid_search_20240129_212910/embeddings_all-MiniLM-L6-v2.pkl. Reusing them.


100%|██████████| 11411/11411 [00:23<00:00, 489.78it/s]


In [63]:
training_dataset.X_bow.todense().shape

(75499, 2000)